## Transport calculation using EPWpy

<table>
<tr>
<td width="50%">

Author: **Sabyasachi Tiwari**


In this notebook, we compute the phonon-limited carrier mobility of silicon using the ab initio Boltzmann Transport Equation (BTE). Electrons and phonons are computed with Quantum ESPRESSO (QE), maximally-localized Wannier functions are computed with Wannier90, and transport properties are computed with EPW. Steps in **bold** are mandatory while steps not in bold can be skipped. However, we reccommend going through all steps for an overall learning experience.
    
    
</td>
<td width="50%">

**MATCSSI**

<img src="https://matcssi.tacc.utexas.edu/media/filer_public_thumbnails/filer_public/9f/1e/9f1ebcd2-8f80-4142-bcdf-b9c262c6b62d/matccsi-home-banner.jpg__1400x1400_q85_subsampling-2.jpg" width="1000">

For running dense calculations

please visit [MATCSSI](https://matcssi.tacc.utexas.edu/)


</td>
</tr>
</table>

## NOTE: 

This notebook assumes that EPWpy is already installed in your active environment and that you are using the corresponding Jupyter kernel.
If you need guidance on installation or environment setup, please refer to the `installation_setup.ipynb` notebook.

## Phonon-limited carrier mobility in semiconductors

From here onwards we compute the phonon-limited carrier mobility of silicon using the _ab initio_ Boltzmann Transport Equation (BTE). Electrons and phonons are computed with Quantum ESPRESSO (QE), maximally-localized Wannier functions are computed with Wannier90, and transport properties are computed with EPW. 

Below we define constants that will remail unchanged throughout the Notebook. The object `silicon` is created as an instance of the `EPWpy` class. This object will contain everything that we need to execute and analyze the calculations.

In [ ]:
from EPWpy import EPWpy as EP

silicon = EP.EPWpy({'structure_mp':"mp-149"},
                   system = 'si')


### A few sanity checks
We check the lattice structure, atomic positions and atomic species. We also check the location of QE executables if they are correctly obtained by EPWpy

In [ ]:
print(silicon.structure_params_summary)
print('code location: ',silicon.code)
print('environment: ', silicon.env)

In [ ]:
%matplotlib widget

app = silicon.display_lattice(supercell=[2,2,2],
                              view={'wrap':False,
                                    'show_bond_length':False,
                                    'show':True,
                                    'atom_size_factor':100})


### Self-consistent field (SCF) calculations

Here we perform the self-consistent field calculation to obtain the electron charge density of silicon in the ground state. The calculation consists of three separate steps:
1. Apply the method `scf` to the object `silicon`. This step specifies runtime parameters for an SCF calculation on siicon 
2. Based on the properties defined at step 1 as well as other properties that are set by default within EPWpy, the method `prepare` creates the input file needed by QE
3. The method `run` applied to the object `silicon` instructs QE to perform the SCF calculation

In [ ]:
silicon.verbosity = 2
silicon.run_serial = True  # Run calculations synchronously 
silicon.scf(name='scf',kpoints={'kpoints':[[6,6,6]]})
silicon.prepare(1,type_run='scf')
silicon.run(16,type_run='scf',parallelization='-nk 4')
silicon.pw_util = silicon.PW_utilities()

#silicon.display_file('si/scf/scf.out')

### Band structure calculation

In this step, we compute the band structure of silicon along some high-symmetry lines in the Brillouin zone.

This calculation is not strictly necessary to compute the mobility, but it is useful to understand the electronic structure of the system under consideration.

Also in this case, we use **three instructions** to specify runtime parameters, prepare the input file, and execute the QE calculation.

In [ ]:
silicon.scf(control={'calculation':'\'bands\''},
            system={'nbnd':12},
            kpoints={'kpoints':[
                                ['0.5','0.50','0.50','20'],
                                ['0.0','0.00','0.00','20'],
                                ['0.5','0.25','0.75','20']
                               ],
                     'kpoints_type':'{crystal_b}'
                    },
            name='bs')
silicon.prepare(type_run='bs')
silicon.run(16,type_run='bs',parallelization='-nk 4')

### Band structure plot

We now plot the electronic band structure computed at the previous step. The zero of the energy axis is set to the value specified manually via `ef0`.


In [ ]:
from EPWpy.QE.band_util import BandUtil## get band plotting utility 

bnd_util = BandUtil('si','si')
bnd_util.plot_band_QE(xticks=['L','G','X'])


### Phonon dispersion relations

To compute phonon-limited mobilities, we need to determine vibrational frequencies and eigenmodes. This operation consists of three steps
1. We compute these properties on a uniform and centered Brillouin zone grid
2. We perform a Fourier transform of the results in order to obtain the interatomic force constants (IFCs)
3. We interpolate the IFCs along specified Brillouin zone paths to obtain phonon dispersions.

This plot of phonon dispersions is only meant for us to develop a qualitative understanding of the vibrational properties of the system under consideration. The phonon interpolation needed for transport calculations is performed once again later by EPW.

#### Step 1: Calculations of phonons on uniform Brillouin zone grid

In [ ]:
silicon.ph(phonons={'fildyn':'\'si.dyn\'',
                    'nq1':3,
                    'nq2':3,
                    'nq3':3,
                    'fildvscf':'\'dvscf\''}
          )
silicon.prepare(type_run='ph')
silicon.run(48,type_run='ph',parallelization='-nk 4')            

#### Step 2: Generation of IFCs

In [ ]:
silicon.q2r(name='q2r')
silicon.prepare(type_run='q2r')
silicon.run(1,type_run='q2r')

In [ ]:
silicon.dynmat({'fildyn':'\'si.dyn1\''},
               name='dynmat')
silicon.prepare(1,'dynmat')
silicon.run(4,'dynmat')

#### Step 2.5 Visualize phonon-vibration 
We first choose the polarization vector using the Phonon utilities 

In [ ]:
import numpy as np 
silicon.ph_util = silicon.PH_utilities() # Get the PH utilities
print(silicon.ph_util.__dict__)   # This dictionary shows what attributes the ph_util has
pl_vec = silicon.ph_util.polarization_vector[:,:,3:] # We get the polarization vector
print(np.shape(pl_vec))

The pl_vec has a shape (nmodes, natoms, direction).
We visualize the LO mode of Si below

In [ ]:
from EPWpy.utilities.display_struct import *

Data = silicon.get_Data(pl_vec[3,:,:],supercell=[3,3,3]) # We visualize for a supercell
fig, ani = animate_crystal_phonon(Data, alpha = 6, view = {'wrap':False,
                                    'bond_length':3.6,
                                    'show_bond_length':False,'quiver_length':25})


#### Step 3: Interpolation of IFCs and generation of phonon dispersions plot

The logic and syntax of this operation are the same as for the band structure plot above: three instructions to execute `matdyn.x` and then plotting.

In [ ]:
silicon.matdyn(name='matdyn',
               kpoints={'kpoints':[
                                   ['0.5','0.50','0.50','20'],
                                   ['0.0','0.00','0.00','20'],
                                   ['0.5','0.25','0.75','20']
                                 ],
                        'kpoints_type':'{crystal_b}'
                       },

              )
silicon.prepare(type_run='matdyn')
silicon.run(1,type_run='matdyn')          


In [ ]:
bnd_util.plot_phonon_QE(xticks=['L','$\Gamma$','X'])

### Transformation of electrons and phonons to Wannier basis with EPW

Now we have Kohn-Sham wavefunctions and variations of the self-consistent Kohn-Sham potential on coarse Brillouin zone grid. We will generate the electron Hamiltonian, the IFCs, and the electron-phonon matrix elements in the Wannier representation using [EPW](https://epw-code.org/). Details on the underlying formalism can be found [here](https://arxiv.org/abs/1603.06965) (free version) or [here](https://doi.org/10.1103/RevModPhys.89.015003) (journal version).

This operation involves four logicals steps:
1. Compute Kohn-Sham states on a uniform centered Brillouin zone grid (QE)
2. Use EPW to load these states and call Wannier90 to generate Wannier functions
3. Use EPW to load IFCs and potential variations, and combine with 2. to compute electron-phonon matrix elements in the Bloch representation
4. Use EPW to perform the transformation to the Wannier basis and write to file

#### Step 1: Calculations of Kohn-Sham states on uniform Brillouin zone grid

In [ ]:
silicon.nscf(system={'nbnd':8},
             kpoints={'grid':[6,6,6],'kpoints_type': 'crystal'})
silicon.prepare(type_run='nscf')
silicon.run(16,type_run='nscf',parallelization = '-nk 4')             

#### Steps 2-4: Load Bloch representation, Wannierize, write to file quantities in Wannier representation

In [ ]:
# File with k-path for sanity checks
silicon.filkf_file = 'LGX.txt'
silicon.epw(epwin={'wdata':['guiding_centres = .true.',
                            'use_ws_distance = T'],
                   'proj':['\'Si : sp3\''],
                   'band_plot':'.true.',
                   'filkf':f'\'{silicon.filkf_file}\'',
                   'filqf':f'\'{silicon.filkf_file}\'',
                   'wannierize':'.true.', 
                   'elph':'.true.',           
                   'num_iter':500,
                   'wannier_plot':'.true.',
                   'wannier_plot_radius':'5.0',  
                   'refresh':True                # Refresh the inputs to have a clean calculation
                  },
            name='epw1')
silicon.filkf_file = 'LGX.txt'
silicon.filkf(path=[[0.5,0.5,0.5],
                    [0.0,0.0,0.0],
                    [0.5,0.25,0.75]],
              length=[51,51],                   
             )
silicon.prepare(type_run='epw1') 
silicon.run(48,type_run='epw1')

#### Sanity check: Interpolated bands and phonons from EPW

At this point we have all necessary quantities in the Wannier representation on file. As a sanity check, we perform a simple interpolation of bands and phonons to make sure that we reproduce the results found above _without_ Wannier interpolation.


In [ ]:
# Electrons

bnd_util.plot_band_QE(xticks=['L','G','X'], first = True,linestyle='--')
bnd_util.plot_band_EPW(xticks=['L','G','X'], first = False)


# Phonons
bnd_util.plot_phonon_QE(xticks=['L','G','X'], first = True,linestyle='--')
bnd_util.plot_phonon_EPW(xticks=['L','G','X'], first = False)



#### Visualizing Wannier orbitals

We now visualize Wannier orbitals

In [ ]:
from EPWpy.utilities import *
silicon.EPWutil = silicon.EPW_utilities()
silicon.EPWutil.plot_wannier('si_00005.cube')
help(silicon.EPWutil.plot_wannier)

### Calculation of carrier mobility

In order to compute the carrier mobility, we perform the following operations:
1. We interpolate the electrons, phonons, and electron-phonon couplings onto a fine Brillouin zone grid (60 x 60 x 60 for electrons and phonons in this example)
2. We use these data to solve the BTE within EPW

Both steps are performed within a single call of EPW. Note the keyword `temps` which is used to perform calculations for multiple temperatures (300 K, ..., 100 K in this example).

In [ ]:
#silicon.reset()
silicon.epw(epwin={'elph':'.true.',               
                   'etf_mem': '1',
                   'nkf1':40,   
                   'nkf2':40,   
                   'nkf3':40,
                   'nqf1':40,
                   'nqf2':40,
                   'nqf3':40,    
                   'mp_mesh_k':'.true.',
                   'efermi_read':'.true.',
                   'fsthick': 0.3,
                   'fermi_energy':6.6,  # We choose this value close to conduction band
                   'temps':'300 250 200 150 100',
                   'degaussw':0.0, 
                   'transport_calc': 'electron','clean_transport':True,'refresh':False,
                   'nstemp': 5},
            name='epw2')
silicon.prepare(type_run='epw2')
silicon.run(48,type_run='epw2',parallelization='-nk 12 -ni 4') # We utilize the two-level parallelism in EPW with 12 k and 4 q point distribution

### We now plot the mobility and the relaxation rate using EPW_utilities

There are three steps
1. Defining the utilitiy object
2. We plot the relaxation rate as a function of energy w.r.t. conduction band minima
3. We plot the mobility as a function of temperature




In [ ]:
import matplotlib.pyplot as plt
import numpy as np
silicon.epw_params['temps'] = 300.0   # We get the property for a particular temperature
silicon.ep_util = silicon.EPW_utilities()
transport=silicon.ep_util.transport()
print('Available properties',transport.keys())

In [ ]:
#silicon.reset() 
%matplotlib inline
plt.close('all')
inv_tau = transport['relaxation_time_elec']

plt.scatter(inv_tau[:,3],inv_tau[:,4])
plt.grid()
plt.ylabel('Relaxation rate (1/ps)')
plt.xlabel('Energy (eV)')

plt.axis([6.5,6.9,0,20])
plt.show()


In [ ]:
%matplotlib inline

silicon.epw_fold = 'epw'
silicon.epw_file = 'epw2'
temps=[300, 250, 200, 150, 100]          
mob=[]
font=16
for T in temps:
    silicon.epw_params['temps']=T              
    print(silicon.ibte_mobility_e[0,0],T)      
    mob.append(silicon.ibte_mobility_e[1,1])
    plt.scatter(T,silicon.ibte_mobility_e[1,1], color = 'crimson')    # If you have error/ comment these two lines
    plt.scatter(T,silicon.serta_mobility_e[1,1], color = 'royalblue') #

plt.plot(temps[::-1],mob[::-1], color = 'crimson')
plt.grid()
plt.xticks([100,150,200,250,300],fontsize=font)
plt.yticks([1000,2000,3000,4000],fontsize=font)
plt.xlabel('Temperature (K)',fontsize=16)
plt.ylabel('$\mu$ (cm$^2$V$^{-1}$s$^{-1}$)',fontsize=16)
plt.xticks(fontsize=16)
plt.yticks(fontsize=16)
plt.show()

### Can you find the effect of fsthick from 0.1 to 0.3 eV on mobility with minimal change? 
Hint: You need to rerun epw with changing fsthick in a for loop 